In [ ]:
from transformers import  AutoModel,AutoTokenizer,AutoModelForSequenceClassification ,AutoConfig, Trainer,TrainingArguments,\
BitsAndBytesConfig,pipeline,default_data_collator,DataCollatorWithPadding,DataCollatorForLanguageModeling
from transformers.utils import move_cache
from chat_template_utils import get_json_schema
from llama_cpp import Llama
from utils import *
from peft import *
import datasets
from datasets import Features, Value
import torchmetrics
import torch
from torch.utils.data.dataloader import DataLoader,Dataset
from hqq.engine.hf import HQQModelForCausalLM
from hqq.models.hf.base import AutoHQQHFModel
from huggingface_hub import snapshot_download
import deepspeed
import os
import pandas as pd
import json
from var_dump import var_dump
from bs4 import BeautifulSoup,PageElement,Comment
import matplotlib.pyplot as plt
import seaborn as sns
import langchain
from bertopic import BERTopic

cache_dir='/var/tmp/.cache/' #'/proj/ciptmp/ix05ogym/.cache/'
output_dir = cache_dir+'outputs/'

move_cache(cache_dir)

def pd_full_screen():
    pd.set_option('display.max_rows', None)
    pd.set_option('display.max_columns', None)
    
def pd_normal_screen():
    pd.set_option('display.max_rows', 10)
    pd.set_option('display.max_columns', 5)



In [ ]:
df = pd.read_excel('alldata_cleaned.xlsx',dtype={'query':str,'element':str},index_col=0)
c = df['element'].str.contains('<form')
df = df[~c].drop_duplicates(['query']).reset_index(drop=True)

c2 = df['element'].str.contains('<a')

def link(x):
    a = BeautifulSoup(str(x['element']),'html.parser').find('a')
    return {'query':a.text.lower().strip(),'element':a}
d = df[c2].apply(link,axis=1)
d= pd.DataFrame(d.tolist())
d

In [ ]:
from sentence_transformers  import SentenceTransformer,CrossEncoder
model_name = 'cross-encoder/stsb-roberta-large'#'cross-encoder/msmarco-MiniLM-L12-en-de-v1'#'cross-encoder/nli-distilroberta-base'
#model = AutoModelForSequenceClassification.from_pretrained(model_name,cache_dir=cache_dir)
#config = AutoConfig.from_pretrained(model_name,cache_dir=cache_dir)
model = CrossEncoder(model_name,cache_dir=cache_dir,device='cuda')
#model
model

In [ ]:
queries=['sign in','log in','sign up','register','apply now','next','continue','cookie','accept cookie']
df = {}
for query in queries:
    inp = [[query,q['query']] for i,q in d.iterrows()]
    preds = model.predict(inp)
    df[query]=preds


In [ ]:
df = pd.DataFrame.from_dict(df)
df

In [23]:
pd_full_screen()
d['label']= df.idxmax(1)
d['label_value'] = df.max(axis=1)
c = d['label_value']<0.75
d[c].sort_values('label_value',ascending=False)

query  \
9550                                   apply to this job   
9549                                   apply to this job   
1805                                   apply to this job   
1807                                   apply to this job   
9556                                   apply to this job   
11144                                 registreer / login   
8314   ausbildung geomatiker (m/w/x) ausbildung geoma...   
4989                                        how to apply   
3289                                        how to apply   
7371                                        how to apply   
10250                                       how to apply   
7815                             current associate login   
8987     already have an account? click here to sign in!   
977                                         applications   
3741                                        applications   
2597   связаться с намибеседовать в чате, принимать у...   
9591                                  apply for this job   
13587                                 apply for this job   
796                                   apply for this job   
797                                   apply for this job   
11478                                 apply for this job   
700                                   apply for this job   
698                                   apply for this job   
691                                   apply for this job   
690                                   apply for this job   
689                                   apply for this job   
13830                                 apply for this job   
13297                                 apply for this job   
13288                                 apply for this job   
8656                                  apply for this job   
220                                   apply for this job   
219                                   apply for this job   
9620                                  apply for this job   
3976                                  apply for this job   
9738                                  apply for this job   
13217                                 apply for this job   
9740                                  apply for this job   
19                                    apply for this job   
17                                    apply for this job   
10041                                 apply for this job   
12451                                 apply for this job   
10057                                 apply for this job   
10088                                 apply for this job   
10098                                 apply for this job   
2272                                  apply for this job   
3975                                  apply for this job   
2271                                  apply for this job   
2270                                  apply for this job   
2269                                  apply for this job   
8411                                  apply for this job   
2937                                  apply for this job   
9430                                  apply for this job   
9481                                  apply for this job   
8774                                  apply for this job   
2813                                  apply for this job   
2811                                  apply for this job   
2938                                  apply for this job   
8391                                  apply for this job   
8392                                  apply for this job   
1452                                      search & apply   
8956                                      create account   
6188                                      create account   
787                                  general application   
7575                                  online application   
6028                                  online application   
6679                                  online application   
9470                           

In [ ]:
d['res']=res#[:,1]
pd_full_screen()
d.sort_values('res',ascending=False)
